In [1]:
import pandas as pd
import requests
from urllib.parse import urlparse, parse_qs
import os
from pydrive.auth import GoogleAuth

from pydrive.drive import GoogleDrive

import json

In [2]:
gauth = GoogleAuth()
gauth.LocalWebserverAuth()

drive = GoogleDrive(gauth)

Your browser has been opened to visit:

    https://accounts.google.com/o/oauth2/auth?client_id=911515843534-tovhamtddg2t9f43fk19k21t0kj7cnon.apps.googleusercontent.com&redirect_uri=http%3A%2F%2Flocalhost%3A8080%2F&scope=https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive&access_type=offline&response_type=code

Authentication successful.


In [6]:
data=pd.read_csv('./results_txt/DearAbby.csv',sep=";")

In [7]:
data.head()

Author  Category Subcategory  \
0  Abigail Van Buren (Jeanne Phillips)  Coaching      Advice   
1  Abigail Van Buren (Jeanne Phillips)  Coaching      Advice   
2  Abigail Van Buren (Jeanne Phillips)  Coaching      Advice   
3  Abigail Van Buren (Jeanne Phillips)  Coaching      Advice   
4  Abigail Van Buren (Jeanne Phillips)  Coaching      Advice   

                            title  video  text  download_url  \
0  DEAR ABBY: My significant othe    NaN   NaN           NaN   
1  DEAR ABBY: My husband and I ha    NaN   NaN           NaN   
2  DEAR ABBY: My husband, "Dan,"     NaN   NaN           NaN   
3  DEAR ABBY: I am 30 weeks pregn    NaN   NaN           NaN   
4  DEAR ABBY: Our daughter has be    NaN   NaN           NaN   

                                     transcript_link  flag  count_prompts  
0  https://drive.google.com/file/d/1hDAVJBLJfbJUF...   NaN              1  
1  https://drive.google.com/file/d/1MEll3Yds5jmhY...   NaN              1  
2  https://drive.google.com/file/d/1KwWcRYC-wx6RA...   NaN              1  
3  https://drive.google.com/file/d/1lNpq1TJt5MJ6C...   NaN              1  
4  https://drive.google.com/file/d/1vhahvRKIxW2ns...   NaN              1

In [8]:
links=list(data['transcript_link'])

In [55]:
links[3]

'https://drive.google.com/uc?id=15_3Ua-b_DFRTYVJxs8ea3Zlfj-S1Vsny'

In [56]:
flags=[i.replace(' - coach','')  for i in list(data['flag'])]

In [57]:
links_id=[parse_qs(urlparse(i).query)['id'][0] for i in links ]

In [58]:
def read_textfiles(id,file_name='file.txt'):
    downloaded = drive.CreateFile({'id': id})
    downloaded.GetContentFile(file_name)
    file_path=f'./{file_name}'
    with open(file_path, 'r') as file:
        content = file.read()
    os.remove(file_path)
    return content
    
            

In [59]:
def convert_to_prompt_completion_pairs(text, flag):
    pairs = []
    lines = text.strip().split('\n')

    if flag == "speaker A":
        current_prompt = None
        for line in lines:
            if line.startswith("Speaker A:"):
                current_prompt = line[len("Speaker A:") + 1:].strip()
            elif line.startswith("Speaker B:"):
                completion = line[len("Speaker B:") + 1:].strip()
                if current_prompt:
                    pairs.append({"prompt": current_prompt, "completion": completion})
    
    elif flag == "speaker B":
        current_prompt = None
        for line in lines:
            if line.startswith("Speaker B:"):
                current_prompt = line[len("Speaker B:") + 1:].strip()
            elif line.startswith("Speaker A:"):
                completion = line[len("Speaker A:") + 1:].strip()
                if current_prompt:
                    pairs.append({"prompt": current_prompt, "completion": completion})

    return pairs

In [60]:
pairs=[]
for id,flag in zip(links_id,flags):
    pairs.append(convert_to_prompt_completion_pairs(read_textfiles(id),flag))

In [61]:
pairs

[[{'prompt': "You. I'm John Malouf. Today I'm talking with psychologist Emma Slade about acceptance and commitment therapy. Emma, tell us about yourself.",
   'completion': 'I work as a psychologist for a company called Weight Management Psychology in Brisbane.'},
  {'prompt': "And you're going to tell us today about a specific client and how you applied acceptance and commitment therapy.",
   'completion': "Okay, yeah, so I've been working with a client. We'll call her Jen, and she's 18 years of age. And she first came to session, she was exercising, but struggling to exercise more, and she couldn't quite work out why."},
  {'prompt': 'And so what was the goal for her? What did she want to accomplish with you?',
   'completion': "Yeah, so she came in and she spoke about going to a particular exercise class that she really loved, but she wanted to go five times a week. But finding that she was going once or twice a week, and to her, it just kind of didn't make sense as to she really lo

In [62]:
pairs[0]

[{'prompt': "You. I'm John Malouf. Today I'm talking with psychologist Emma Slade about acceptance and commitment therapy. Emma, tell us about yourself.",
  'completion': 'I work as a psychologist for a company called Weight Management Psychology in Brisbane.'},
 {'prompt': "And you're going to tell us today about a specific client and how you applied acceptance and commitment therapy.",
  'completion': "Okay, yeah, so I've been working with a client. We'll call her Jen, and she's 18 years of age. And she first came to session, she was exercising, but struggling to exercise more, and she couldn't quite work out why."},
 {'prompt': 'And so what was the goal for her? What did she want to accomplish with you?',
  'completion': "Yeah, so she came in and she spoke about going to a particular exercise class that she really loved, but she wanted to go five times a week. But finding that she was going once or twice a week, and to her, it just kind of didn't make sense as to she really loved th

In [63]:
result = []
for element in pairs:
    result.extend(element)

In [66]:
result[2]

{'prompt': 'And so what was the goal for her? What did she want to accomplish with you?',
 'completion': "Yeah, so she came in and she spoke about going to a particular exercise class that she really loved, but she wanted to go five times a week. But finding that she was going once or twice a week, and to her, it just kind of didn't make sense as to she really loved this exercise class, but she couldn't find the motivation, as she termed it, to go more."}

In [21]:

with open('therapies.json', 'w') as outfile:
    for i in result:
        json.dump(i, outfile)
    outfile.write('\n')


In [20]:
print(print)

<built-in function print>


In [34]:


data = []
with open("therapies_new_prepared_final.jsonl", 'r', encoding='utf-8') as f:
    for line in f:
        data.append(json.loads(line))

In [41]:
data[0]

{'prompt': "You. I'm John Malouf. Today I'm talking with psychologist Emma Slade about acceptance and commitment therapy. Emma, tell us about yourself. ->",
 'completion': ' I work as a psychologist for a company called Weight Management Psychology in Brisbane.\n'}

In [39]:
import re
def validate_jsonl(fine_tune_data, validate_api=True, prompt_separator="->", completion_stop="STOPSTOP"):
    if not fine_tune_data:
        return False
    output = []
    count = 0
    validated_line = False
    regex_to_validate = re.compile('')

    if validate_api:
        regex_to_validate = re.compile(r'^\{"prompt":\s*"([^"]+)\s*{}",\s*"completion":\s*"\s([^"]+)\s*{}"\s*\}$'.format(prompt_separator, completion_stop))
    else:
        regex_to_validate = re.compile(r'^\{"prompt":\s*"([^"]+)",\s*"completion":\s*"([^"]+)"\s*\}$')

    for line in fine_tune_data.split("\r\n"):
        count += 1
        validated_line = bool(regex_to_validate.match(line))
        output.append({'count': count, 'valid': validated_line, 'line': line})

    return output

In [44]:
!pip install tiktoken


[notice] A new release of pip available: 22.3.1 -> 23.2.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [45]:
%pip install --upgrade tiktoken

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip available: 22.3.1 -> 23.2.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [48]:
import tiktoken
encoding = tiktoken.get_encoding("cl100k_base")

In [49]:
encoding = tiktoken.encoding_for_model("gpt-3.5-turbo")

In [70]:
len(encoding.encode(result[2]['prompt']+' '+result[2]['completion']))

99

In [72]:
def num_tokens_from_string(input_element, encoding_name: str) -> int:
    """Returns the number of tokens in a text string."""
    encoding = tiktoken.get_encoding(encoding_name)
    num_tokens = len(encoding.encode(input_element))
    return num_tokens

In [94]:
num_tokens=[num_tokens_from_string(result[i]['prompt']+' '+result[i]['completion'],"cl100k_base") for i in range(0,700)]

In [95]:
sum(num_tokens)

147152

In [97]:
(sum(num_tokens)/1000)*0.0001 

0.0147152

In [101]:
!python.exe -m pip install --upgrade pip

  Using cached pip-23.2.1-py3-none-any.whl (2.1 MB)
  Attempting uninstall: pip
    Found existing installation: pip 22.3.1
    Uninstalling pip-22.3.1:
      Successfully uninstalled pip-22.3.1


In [104]:
!pip install setuptools

In [106]:
!pip install autotrain-advanced==0.6.2

ERROR: Could not find a version that satisfies the requirement triton==2.0.0.post1 (from autotrain-advanced) (from versions: none)
ERROR: No matching distribution found for triton==2.0.0.post1



  Obtaining dependency information for autotrain-advanced==0.6.2 from https://files.pythonhosted.org/packages/b3/84/57f4cac165394e2c99967c469170d19651ec05f8c762489c70088897c091/autotrain_advanced-0.6.2-py3-none-any.whl.metadata
  Using cached autotrain_advanced-0.6.2-py3-none-any.whl.metadata (7.9 kB)
  Using cached albumentations-1.3.0-py3-none-any.whl (123 kB)
  Obtaining dependency information for codecarbon==2.2.3 from https://files.pythonhosted.org/packages/91/21/aefc136fa14595668f62c3008789555a4de900f3e23cbf7214743e6c728a/codecarbon-2.2.3-py3-none-any.whl.metadata
  Using cached codecarbon-2.2.3-py3-none-any.whl.metadata (6.5 kB)
  Obtaining dependency information for datasets[vision]~=2.13.0 from https://files.pythonhosted.org/packages/12/17/95e48481a826f85c918e0610257de493164096e29fe16ec408c0b862e057/datasets-2.13.1-py3-none-any.whl.metadata
  Using cached datasets-2.13.1-py3-none-any.whl.metadata (20 kB)
  Using cached evaluate-0.3.0-py3-none-any.whl (72 kB)
  Using cached ip

In [ ]:
autotrain setup --update-torch